In [267]:
import numpy as np
import pandas as pd
from tqdm import tqdm
from sklearn.model_selection import train_test_split, cross_val_score, StratifiedKFold, RandomizedSearchCV
from sklearn.linear_model import LinearRegression, LogisticRegression, Ridge, Lasso
from sklearn.preprocessing import MinMaxScaler, StandardScaler, OneHotEncoder, OrdinalEncoder
from sklearn.metrics import accuracy_score, get_scorer_names, confusion_matrix, classification_report
from sklearn.tree import DecisionTreeClassifier
from sklearn import tree
from sklearn.model_selection import GridSearchCV
from sklearn.neighbors import KNeighborsClassifier
from sklearn.ensemble import BaggingClassifier, RandomForestClassifier, AdaBoostClassifier, GradientBoostingClassifier, VotingClassifier
from sklearn.ensemble import HistGradientBoostingClassifier, ExtraTreesClassifier
from sklearn.ensemble import StackingClassifier
from sklearn.naive_bayes import GaussianNB, CategoricalNB
from sklearn.feature_selection import SelectKBest, chi2, mutual_info_classif
from xgboost import XGBClassifier
import xgboost as xgb
import matplotlib.pyplot as plt
import seaborn as sns
from sklearn.pipeline import Pipeline
from imblearn.over_sampling import SMOTE
import warnings
warnings.simplefilter(action='ignore', category=FutureWarning)
from statistics import mode as md
from matplotlib import pyplot as plt
from IPython.display import clear_output, display_html 
from collections import Counter
from pprint import pprint

In [63]:
class color:
   PURPLE = '\033[95m'
   CYAN = '\033[96m'
   DARKCYAN = '\033[36m'
   BLUE = '\033[94m'
   GREEN = '\033[92m'
   YELLOW = '\033[93m'
   RED = '\033[91m'
   BOLD = '\033[1m'
   UNDERLINE = '\033[4m'
   END = '\033[0m'

In [64]:
testing = pd.read_csv("tanzanian_water_wells/X_test.csv")
X = pd.read_csv("tanzanian_water_wells/X_train.csv")
y = pd.read_csv("tanzanian_water_wells/y_train.csv")['status_group'].map({'functional': 2, 'functional needs repair': 0, 'non functional': 1})

In [65]:
#Dropping unecessary columns
X = X.drop(['id', 'wpt_name', 'subvillage', 'installer', 'funder', 'scheme_name', 'ward', 'date_recorded', 'recorded_by'], axis=1)
testing = testing.drop(['id', 'wpt_name', 'subvillage', 'installer', 'funder', 'scheme_name', 'ward', 'date_recorded', 'recorded_by'], axis=1)

# Eliminating null values from X_train
X.scheme_management.fillna("None", inplace=True)
X.permit.fillna('Unknown', inplace=True)
X.public_meeting.fillna('Unknown', inplace=True)

# Turning certain dtypes into others
X['permit'] = X['permit'].map({True: 'Yes', False: 'No', 'Unknown': 'Unknown'})
X['gps_height'] = X['gps_height'].astype('float64')
X['population'] = X['population'].astype('float64')
X['construction_year'] = X['construction_year'].astype('int64')
X['region_code'] = X['region_code'].astype('str')
X['district_code'] = X['district_code'].astype('str')

#Defining X_cat
X_cat = X.select_dtypes(exclude=['float64', 'int64'])
X_cat = X_cat.astype('str')
X_cat = pd.get_dummies(X_cat)

#Defining X_numeric
X_numeric = X.select_dtypes(['float64', 'int64'])
scaler = StandardScaler()
scaler.fit(X_numeric)
X_numeric = pd.DataFrame(scaler.transform(X_numeric), columns = X_numeric.columns, index = X_numeric.index)

#Defining X
X = pd.concat([X_numeric, X_cat], axis=1)

#Defining df
df = pd.concat([X, y], axis=1)

#Creating a train-test-split for X and y
X_train, X_test, y_train, y_test = train_test_split(X, y)

#Resampling dataframes for model creation
smote = SMOTE()
X_train_resampled, y_train_resampled = smote.fit_resample(X_train, y_train)
    
X_train = X_train.reset_index(drop=True)
X_test = X_test.reset_index(drop=True)
y_train = y_train.reset_index(drop=True)
y_test = y_test.reset_index(drop=True)
X_train_resampled = X_train_resampled.reset_index(drop=True)
y_train_resampled = y_train_resampled.reset_index(drop=True)
    
df_resampled = pd.concat([X_train_resampled, y_train_resampled], axis=1)

#Separating concatenated dataframe into each status group
f = df_resampled[df_resampled.status_group == 0].reset_index(drop=True).copy()
nf = df_resampled[df_resampled.status_group == 2].reset_index(drop=True).copy()
fnr = df_resampled[df_resampled.status_group == 1].reset_index(drop=True).copy()

#Shuffling all the records
f = f.sample(frac=1)
nf = nf.sample(frac=1)
fnr = fnr.sample(frac=1)

#Splitting each status group into arrays of approximately 1,000 records
fs = [pd.DataFrame(i) for i in np.array_split(f, len(f)//1000)]
nfs = [pd.DataFrame(i) for i in np.array_split(nf, len(nf)//1000)]
fnrs = [pd.DataFrame(i) for i in np.array_split(fnr, len(fnr)//1000)]

#Creating our individual samples for models to train on
resamples = []
for i in range(len(fnrs)):
    resample = pd.concat([fs[i], nfs[i], fnrs[i]])
    resamples.append(resample)

In [66]:
estimators = {'Logistic Regression': LogisticRegression(solver='liblinear', fit_intercept=False), 
              'Decision Tree Classifier': DecisionTreeClassifier(), 
              'K-Nearest Neighbors': KNeighborsClassifier(n_neighbors=3), 
              'Bagging Classifier': BaggingClassifier(estimator=DecisionTreeClassifier(), n_estimators=50, max_features=50), 
              'Random Forest': RandomForestClassifier(), 
              'XG-Boost': XGBClassifier(), 
              'Adaboost': AdaBoostClassifier(estimator=DecisionTreeClassifier(), n_estimators=100, random_state=42), 
              'Gradient Boosted Trees': GradientBoostingClassifier(random_state=42, n_estimators=200, max_features=50), 
              'Extra Randomized Trees': ExtraTreesClassifier(n_estimators=100, random_state=42), 
              'Stacking Classifier': StackingClassifier(
        estimators = [('logistic_regression', LogisticRegression(solver='liblinear', fit_intercept=False)), 
                      ('bagging_classifier', BaggingClassifier(estimator=DecisionTreeClassifier(), n_estimators=50, max_features=50))], 
        final_estimator = XGBClassifier())}

# Approach #1 – Single Model with Original Data

Here we use a single estimator on a training dataset and make predictions on a test dataset.

In [10]:
ap1_dict = {}

for name, estimator in estimators.items():
    
    estimator.fit(X_train, y_train)
    predictions = estimator.predict(X_test)
    matrix = pd.DataFrame(confusion_matrix(y_test, predictions))
    report = pd.DataFrame(classification_report(y_test, predictions, output_dict=True))
    ap1_dict[name] = [predictions, matrix, report]
    
    print(f"Estimator {name} completed.")

Estimator Logistic Regression completed.
Estimator Decision Tree Classifier completed.
Estimator K-Nearest Neighbors completed.
Estimator Bagging Classifier completed.
Estimator Random Forest completed.
Estimator XG-Boost completed.
Estimator Adaboost completed.
Estimator Gradient Boosted Trees completed.
Estimator Extra Randomized Trees completed.
Estimator Stacking Classifier completed.


# Approach #2 – Single Model with Resampled Data

Here we use a single estimator on a resampled training dataset and make predictions on a test dataset.

In [28]:
smote = SMOTE()

In [11]:
ap2_dict = {}

for name, estimator in estimators.items():
    
    estimator.fit(X_train_resampled, y_train_resampled)
    predictions = estimator.predict(X_test)
    matrix = pd.DataFrame(confusion_matrix(y_test, predictions))
    report = pd.DataFrame(classification_report(y_test, predictions, output_dict=True))
    ap2_dict[name] = [predictions, matrix, report]
    
    print(f"Estimator {name} completed.")

Estimator Logistic Regression completed.
Estimator Decision Tree Classifier completed.
Estimator K-Nearest Neighbors completed.
Estimator Bagging Classifier completed.
Estimator Random Forest completed.
Estimator XG-Boost completed.
Estimator Adaboost completed.
Estimator Gradient Boosted Trees completed.
Estimator Extra Randomized Trees completed.
Estimator Stacking Classifier completed.


# Approach #3 – Single Model with Resampled Data (Different Ratio)

In [49]:
strategy = {0: 10000} #optional strategy
smote = SMOTE(sampling_strategy=strategy)
X_train_resampled, y_train_resampled = smote.fit_resample(X_train, y_train)

In [50]:
ap3_dict = {}

for name, estimator in estimators.items():
    
    estimator.fit(X_train_resampled, y_train_resampled)
    predictions = estimator.predict(X_test)
    matrix = pd.DataFrame(confusion_matrix(y_test, predictions))
    report = pd.DataFrame(classification_report(y_test, predictions, output_dict=True))
    ap3_dict[name] = [predictions, matrix, report]
    
    print(f"Estimator {name} completed.")

Estimator Logistic Regression completed.
Estimator Decision Tree Classifier completed.
Estimator K-Nearest Neighbors completed.
Estimator Bagging Classifier completed.
Estimator Random Forest completed.
Estimator XG-Boost completed.
Estimator Adaboost completed.
Estimator Gradient Boosted Trees completed.
Estimator Extra Randomized Trees completed.
Estimator Stacking Classifier completed.


# Approach #4 – Single Model with Resampled Data (Different Ratio)

In [51]:
strategy = {0: 15000} #optional strategy
smote = SMOTE(sampling_strategy=strategy)
X_train_resampled, y_train_resampled = smote.fit_resample(X_train, y_train)

In [52]:
ap4_dict = {}

for name, estimator in estimators.items():
    
    estimator.fit(X_train_resampled, y_train_resampled)
    predictions = estimator.predict(X_test)
    matrix = pd.DataFrame(confusion_matrix(y_test, predictions))
    report = pd.DataFrame(classification_report(y_test, predictions, output_dict=True))
    ap4_dict[name] = [predictions, matrix, report]
    
    print(f"Estimator {name} completed.")

Estimator Logistic Regression completed.
Estimator Decision Tree Classifier completed.
Estimator K-Nearest Neighbors completed.
Estimator Bagging Classifier completed.
Estimator Random Forest completed.
Estimator XG-Boost completed.
Estimator Adaboost completed.
Estimator Gradient Boosted Trees completed.
Estimator Extra Randomized Trees completed.
Estimator Stacking Classifier completed.


# Approach #5 – Single Model with Resampled Data (Different Ratio)

In [53]:
strategy = {0: 20000} #optional strategy
smote = SMOTE(sampling_strategy=strategy)
X_train_resampled, y_train_resampled = smote.fit_resample(X_train, y_train)

In [54]:
ap5_dict = {}

for name, estimator in estimators.items():
    
    estimator.fit(X_train_resampled, y_train_resampled)
    predictions = estimator.predict(X_test)
    matrix = pd.DataFrame(confusion_matrix(y_test, predictions))
    report = pd.DataFrame(classification_report(y_test, predictions, output_dict=True))
    ap5_dict[name] = [predictions, matrix, report]
    
    print(f"Estimator {name} completed.")

Estimator Logistic Regression completed.
Estimator Decision Tree Classifier completed.
Estimator K-Nearest Neighbors completed.
Estimator Bagging Classifier completed.
Estimator Random Forest completed.
Estimator XG-Boost completed.
Estimator Adaboost completed.
Estimator Gradient Boosted Trees completed.
Estimator Extra Randomized Trees completed.
Estimator Stacking Classifier completed.


# Approach #6 – Voting Classifiers on Different Data Samples

After resampling the data, we split it into multiple samples with equal amounts of each status group. An estimator is trained on each sample and makes different predictions for that dataset based on each sample. A mock voting classifier is made from the resulting model predictions.

In [12]:
ap6_dict = {}

In [13]:
for name, est in estimators.items():

    preds = []
    modes=[]
    counters=[]
    
    for i in range(len(resamples)):
        estimator =  est
        X = resamples[i].drop(['status_group'], axis=1)
        y = resamples[i]['status_group']
        estimator.fit(X, y)
        pred = estimator.predict(X_test)
        preds.append(pred)

        clear_output(wait=True)
        print(f"Sample: #{i}")
        print(f"Estimator: {name}")
        clear_output(wait=True)


    for i in range(len(preds[0])):
        counter = Counter([pred[i] for pred in preds])
        counters.append(counter)

    counter_modes = []
    for counter in counters:
        counter_mode = sorted(counter.items(), key=lambda x: [x[1], x[0]], reverse=True)[0][0]
        counter_modes.append(counter_mode)

    matrix = pd.DataFrame(confusion_matrix(y_test, counter_modes))
    report = pd.DataFrame(classification_report(y_test, counter_modes, output_dict=True))
    
    ap6_dict[name] = [preds, counter_modes, matrix, report]

Sample: #23
Estimator: Stacking Classifier


# Looking at All of our Approaches

In [56]:
master_dict = {}
for name in estimators.keys():
    ap1 = ap1_dict[name][2]
    ap2 = ap2_dict[name][2]
    ap3 = ap3_dict[name][2]
    ap4 = ap4_dict[name][2]
    ap5 = ap5_dict[name][2]
#     ap6 = ap6_dict[name][3]
    master_dict[name]=[ap1,ap2,ap3,ap4,ap5]
    
print("\n")
for name, results in master_dict.items():
    print(color.BOLD + name + color.END)
    display(results[0].style.set_caption("original data"))
    display(results[1].style.set_caption("resampled data"))
    display(results[2].style.set_caption("resampled data (n = 10000)"))
    display(results[3].style.set_caption("resampled data (n = 15000)"))
    display(results[4].style.set_caption("resampled data (n = 20000)"))
#     display(results[5].style.set_caption("resampled samples"))
    print("\n\n")



Logistic Regression





Decision Tree Classifier





K-Nearest Neighbors





Bagging Classifier





Random Forest





XG-Boost





Adaboost





Gradient Boosted Trees





Extra Randomized Trees





Stacking Classifier


# Picking our Best Models

In [18]:
strategy = {0: 10000}
smote = SMOTE(sampling_strategy=strategy)
X_train_resampled, y_train_resampled = smote.fit_resample(X_train, y_train)

model1 = RandomForestClassifier(n_estimators=100).fit(X_train_resampled, y_train_resampled)
model2 = BaggingClassifier(estimator=DecisionTreeClassifier(), n_estimators=100).fit(X_train, y_train)

preds_1 = model1.predict(X_test)
preds_2 = model2.predict(X_test)

In [19]:
decisions = []
for a, b in list(zip(preds_1, preds_2)):
    decision = None
    if a == b:
        decision = b
    elif a == 0:
        decision = 0
    elif b == 2:
        decision = 2
    else:
        decision = 2
    decisions.append(decision)

pred_df = pd.DataFrame({'random forest': preds_1, 
                        'bagging classifier': preds_2, 
                        'decision': decisions, 
                        'original': y_test})

In [20]:
pd.DataFrame(classification_report(y_test, preds_1, output_dict=True))

0            1            2  accuracy     macro avg  \
precision     0.447695     0.828748     0.816565  0.792929      0.697669   
recall        0.472846     0.777524     0.846049  0.792929      0.698807   
f1-score      0.459927     0.802319     0.831046  0.792929      0.697764   
support    1068.000000  5695.000000  8087.000000  0.792929  14850.000000   

           weighted avg  
precision      0.794708  
recall         0.792929  
f1-score       0.793339  
support    14850.000000

In [101]:
pd.DataFrame(confusion_matrix(y_test, decisions))

0     1     2
0  498   115   489
1  166  4359  1229
2  436   597  6961

In [120]:
preds = estimator.predict(X_test)

[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.8s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.8s finished


In [17]:
pd.DataFrame(confusion_matrix(y_test, preds_1))

NameError: name 'preds_1' is not defined

# Training on fnr-vs-all

Here, we train various models on various versions of our datasets to predict functional-needs-repair cases vs. the rest of them. The sole purpose of this is to maximize predictive power for the least occurring class.

In [144]:
y_train_binarized = y_train.map(lambda x: 1 if x==0 else 0)

dataset_dict = {'original': (X_train, y_train_binarized), 
                 'resample strat=10k': SMOTE(sampling_strategy={1:10000}).fit_resample(X_train, y_train_binarized), 
                 'resample strat=15k': SMOTE(sampling_strategy={1:15000}).fit_resample(X_train, y_train_binarized), 
                 'resample strat=20k': SMOTE(sampling_strategy={1:20000}).fit_resample(X_train, y_train_binarized), 
                 'resample strat=25k': SMOTE(sampling_strategy={1:25000}).fit_resample(X_train, y_train_binarized), 
                 'resampled': SMOTE().fit_resample(X_train, y_train_binarized)}

In [145]:
estimators = {'Logistic Regression': LogisticRegression(solver='liblinear', fit_intercept=False), 
              'Decision Tree Classifier': DecisionTreeClassifier(), 
              'K-Nearest Neighbors': KNeighborsClassifier(n_neighbors=3), 
              'Bagging Classifier': BaggingClassifier(estimator=DecisionTreeClassifier(), n_estimators=50, max_features=50), 
              'Random Forest': RandomForestClassifier(), 
              'XG-Boost': XGBClassifier(), 
              'Adaboost': AdaBoostClassifier(estimator=DecisionTreeClassifier(), n_estimators=100, random_state=42), 
              'Gradient Boosted Trees': GradientBoostingClassifier(random_state=42, n_estimators=200, max_features=50), 
              'Extra Randomized Trees': ExtraTreesClassifier(n_estimators=100, random_state=42)}

In [146]:
estimators = [(name, estimator, dataset_dict) for name, estimator in estimators.items()]

In [148]:
fnr_vs_all = {}

for name, estimator, dataset_dict in estimators:
    
    results = {dataset_name: [] for dataset_name in dataset_dict.keys()}
    
    for dataset_name, dataset_pair in dataset_dict.items():
        
        clear_output(wait=True)
        print(f"Estimator: {name}")
        print(f"Dataset: {dataset_name}")
        clear_output(wait=True)
        
        X = dataset_pair[0]
        y = dataset_pair[1]
        estimator.fit(X, y)
        preds = estimator.predict(X_test)
        matrix = pd.DataFrame(confusion_matrix(y_test_binarized, preds))
        report = pd.DataFrame(classification_report(y_test_binarized, preds, output_dict=True))
        result = (preds, matrix, report)
        results[dataset_name] = result
        
    fnr_vs_all[name] = results

/Users/angeloturri/opt/anaconda3/envs/learn-env/lib/python3.11/site-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/Users/angeloturri/opt/anaconda3/envs/learn-env/lib/python3.11/site-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/Users/angeloturri/opt/anaconda3/envs/learn-env/lib/python3.11/site-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_

In [165]:
fnr_vs_all['Logistic Regression'][dataset_names[0]][0]

array([0, 0, 0, ..., 0, 0, 0])

In [163]:
for name, results in fnr_vs_all.items():
    
    dataset_names = list(results.keys())
    
    report0 = pd.DataFrame(classification_report(y_test_binarized, results[dataset_names[0]][0], output_dict=True))
    report1 = pd.DataFrame(classification_report(y_test_binarized, results[dataset_names[1]][0], output_dict=True))
    report2 = pd.DataFrame(classification_report(y_test_binarized, results[dataset_names[2]][0], output_dict=True))
    report3 = pd.DataFrame(classification_report(y_test_binarized, results[dataset_names[3]][0], output_dict=True))
    report4 = pd.DataFrame(classification_report(y_test_binarized, results[dataset_names[4]][0], output_dict=True))
    report5 = pd.DataFrame(classification_report(y_test_binarized, results[dataset_names[5]][0], output_dict=True))
    
    print(color.BOLD + name + color.END)
    display(report0.style.set_caption(dataset_names[0]))
    display(report1.style.set_caption(dataset_names[1]))
    display(report2.style.set_caption(dataset_names[2]))
    display(report3.style.set_caption(dataset_names[3]))
    display(report4.style.set_caption(dataset_names[4]))
    display(report5.style.set_caption(dataset_names[5]))
#     display(results[5].style.set_caption("resampled samples"))
    print("\n\n")

Logistic Regression





Decision Tree Classifier





K-Nearest Neighbors





Bagging Classifier





Random Forest





XG-Boost





Adaboost





Gradient Boosted Trees





Extra Randomized Trees





Stacking Classifier


In [162]:
for name, results in fnr_vs_all.items():
    
    dataset_names = list(results.keys())
    
    print(color.BOLD + name + color.END)
    display(results[dataset_names[0]][2].style.set_caption(dataset_names[0]))
    display(results[dataset_names[1]][2].style.set_caption(dataset_names[1]))
    display(results[dataset_names[2]][2].style.set_caption(dataset_names[2]))
    display(results[dataset_names[3]][2].style.set_caption(dataset_names[3]))
    display(results[dataset_names[4]][2].style.set_caption(dataset_names[4]))
    display(results[dataset_names[5]][2].style.set_caption(dataset_names[5]))
#     display(results[5].style.set_caption("resampled samples"))
    print("\n\n")

Logistic Regression





Decision Tree Classifier





K-Nearest Neighbors





Bagging Classifier





Random Forest





XG-Boost





Adaboost





Gradient Boosted Trees





Extra Randomized Trees





Stacking Classifier


In [193]:
y_train_binarized_1 = y_train.map(lambda x: 1 if x==0 else 0) #fnr-vs-all
y_train_binarized_2 = y_train.map(lambda x: 1 if x==1 else 0) # nf-vs-all
y_train_binarized_3 = y_train.map(lambda x: 1 if x==2 else 0) # f-vs-all

In [196]:
y_test_binarized_1 = y_test.map(lambda x: 1 if x==0 else 0) #fnr-vs-all
y_test_binarized_2 = y_test.map(lambda x: 1 if x==1 else 0) # nf-vs-all
y_test_binarized_3 = y_test.map(lambda x: 1 if x==2 else 0) # f-vs-all

In [245]:
est = KNeighborsClassifier(n_neighbors=3)
est.fit(X_train, y_train_binarized_1)
ps1_test = est.predict(X_test)
ps1_train = est.predict(X_train)

est = KNeighborsClassifier(n_neighbors=3)
est.fit(X_train, y_train_binarized_2)
ps2_test =  est.predict(X_test)
ps2_train = est.predict(X_train)

est = KNeighborsClassifier(n_neighbors=3)
est.fit(X_train, y_train_binarized_3)
ps3_test =  est.predict(X_test)
ps3_train = est.predict(X_train)

In [248]:
decisions = []

for a, b in list(zip(ps2_test, ps3_test)):
    
    if (a==0) & (b==0):
        decision = 0
        
    elif (a==0) & (b==1):
        decision = 2
        
    elif (a==1) & (b==0):
        decision = 1
        
    elif (a==1) & (b==1):
        decision = 2
        
    decisions.append(decision)

In [250]:
binarized_df = pd.DataFrame({'fnr=1': ps1_train, 'nf=1': ps2_train, 'f=1': ps3_train})

In [270]:
pd.DataFrame(classification_report(y_test, decisions, output_dict=True))

0            1            2  accuracy     macro avg  \
precision     0.377682     0.797999     0.802575  0.767609      0.659419   
recall        0.395683     0.750399     0.830598  0.767609      0.658894   
f1-score      0.386473     0.773468     0.816346  0.767609      0.658762   
support    1112.000000  5633.000000  8105.000000  0.767609  14850.000000   

           weighted avg  
precision      0.769022  
recall         0.767609  
f1-score       0.767891  
support    14850.000000

In [256]:
logreg = LogisticRegression(solver='liblinear', fit_intercept=False)
logreg.fit(binarized_df, y_train)

LogisticRegression(fit_intercept=False, solver='liblinear')

In [261]:
master_preds = logreg.predict(pd.DataFrame({'fnr=1': ps1_test, 'nf=1': ps2_test, 'f=1': ps3_test}))

In [262]:
pd.DataFrame(classification_report(y_test, master_preds, output_dict=True))

0            1            2  accuracy     macro avg  \
precision     0.377682     0.797999     0.802575  0.767609      0.659419   
recall        0.395683     0.750399     0.830598  0.767609      0.658894   
f1-score      0.386473     0.773468     0.816346  0.767609      0.658762   
support    1112.000000  5633.000000  8105.000000  0.767609  14850.000000   

           weighted avg  
precision      0.769022  
recall         0.767609  
f1-score       0.767891  
support    14850.000000

In [264]:
e = RandomForestClassifier()
e.fit(X_train,y_train)

RandomForestClassifier()

In [271]:
# Number of trees in random forest
n_estimators = [int(x) for x in np.linspace(start = 200, stop = 2000, num = 10)]
# Number of features to consider at every split
max_features = ['auto', 'sqrt']
# Maximum number of levels in tree
max_depth = [int(x) for x in np.linspace(10, 110, num = 11)]
max_depth.append(None)
# Minimum number of samples required to split a node
min_samples_split = [2, 5, 10]
# Minimum number of samples required at each leaf node
min_samples_leaf = [1, 2, 4]
# Method of selecting samples for training each tree
bootstrap = [True, False]
# Create the random grid
random_grid = {'n_estimators': n_estimators,
               'max_features': max_features,
               'max_depth': max_depth,
               'min_samples_split': min_samples_split,
               'min_samples_leaf': min_samples_leaf,
               'bootstrap': bootstrap}
pprint(random_grid)

{'bootstrap': [True, False],
 'max_depth': [10, 20, 30, 40, 50, 60, 70, 80, 90, 100, 110, None],
 'max_features': ['auto', 'sqrt'],
 'min_samples_leaf': [1, 2, 4],
 'min_samples_split': [2, 5, 10],
 'n_estimators': [200, 400, 600, 800, 1000, 1200, 1400, 1600, 1800, 2000]}


In [275]:
# Use the random grid to search for best hyperparameters
# First create the base model to tune
rf = RandomForestClassifier()
# Random search of parameters, using 3 fold cross validation, 
# search across 100 different combinations, and use all available cores
rf_random = RandomizedSearchCV(estimator = rf, param_distributions = random_grid, n_iter = 100, cv = 3, verbose=10, random_state=42, n_jobs = -1)
# Fit the random search model
rf_random.fit(X_train, y_train)

Fitting 3 folds for each of 100 candidates, totalling 300 fits


/Users/angeloturri/opt/anaconda3/envs/learn-env/lib/python3.11/site-packages/sklearn/utils/validation.py:767: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if not hasattr(array, "sparse") and array.dtypes.apply(is_sparse).any():
/Users/angeloturri/opt/anaconda3/envs/learn-env/lib/python3.11/site-packages/sklearn/utils/validation.py:767: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if not hasattr(array, "sparse") and array.dtypes.apply(is_sparse).any():
/Users/angeloturri/opt/anaconda3/envs/learn-env/lib/python3.11/site-packages/sklearn/utils/validation.py:767: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if not hasattr(array, "sparse") and array.dtypes.apply(is_sparse).any():
/Users/angeloturri/opt/anaconda3/envs/learn-env/lib/

/Users/angeloturri/opt/anaconda3/envs/learn-env/lib/python3.11/site-packages/sklearn/utils/validation.py:767: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if not hasattr(array, "sparse") and array.dtypes.apply(is_sparse).any():
/Users/angeloturri/opt/anaconda3/envs/learn-env/lib/python3.11/site-packages/sklearn/utils/validation.py:605: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(pd_dtype):
/Users/angeloturri/opt/anaconda3/envs/learn-env/lib/python3.11/site-packages/sklearn/utils/validation.py:614: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(pd_dtype) or not is_extension_array_dtype(pd_dtype):
/Users/angeloturri/opt/anaconda3/envs/learn-env/lib/python3.11/site-packages/sklearn/utils/validation.py:767

/Users/angeloturri/opt/anaconda3/envs/learn-env/lib/python3.11/site-packages/sklearn/utils/validation.py:605: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(pd_dtype):
/Users/angeloturri/opt/anaconda3/envs/learn-env/lib/python3.11/site-packages/sklearn/utils/validation.py:614: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(pd_dtype) or not is_extension_array_dtype(pd_dtype):
/Users/angeloturri/opt/anaconda3/envs/learn-env/lib/python3.11/site-packages/sklearn/utils/validation.py:605: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(pd_dtype):
/Users/angeloturri/opt/anaconda3/envs/learn-env/lib/python3.11/site-packages/sklearn/utils/validation.py:614: FutureWarning: is_sparse is deprecated and will

/Users/angeloturri/opt/anaconda3/envs/learn-env/lib/python3.11/site-packages/sklearn/utils/validation.py:605: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(pd_dtype):
/Users/angeloturri/opt/anaconda3/envs/learn-env/lib/python3.11/site-packages/sklearn/utils/validation.py:614: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(pd_dtype) or not is_extension_array_dtype(pd_dtype):
/Users/angeloturri/opt/anaconda3/envs/learn-env/lib/python3.11/site-packages/sklearn/utils/validation.py:605: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(pd_dtype):
/Users/angeloturri/opt/anaconda3/envs/learn-env/lib/python3.11/site-packages/sklearn/utils/validation.py:614: FutureWarning: is_sparse is deprecated and will

...

/Users/angeloturri/opt/anaconda3/envs/learn-env/lib/python3.11/site-packages/sklearn/utils/validation.py:605: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(pd_dtype):
/Users/angeloturri/opt/anaconda3/envs/learn-env/lib/python3.11/site-packages/sklearn/utils/validation.py:614: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(pd_dtype) or not is_extension_array_dtype(pd_dtype):
/Users/angeloturri/opt/anaconda3/envs/learn-env/lib/python3.11/site-packages/sklearn/utils/validation.py:605: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(pd_dtype):
/Users/angeloturri/opt/anaconda3/envs/learn-env/lib/python3.11/site-packages/sklearn/utils/validation.py:614: FutureWarning: is_sparse is deprecated and will

[CV 2/3; 79/100] START bootstrap=True, max_depth=10, max_features=sqrt, min_samples_leaf=2, min_samples_split=5, n_estimators=1000
[CV 2/3; 79/100] END bootstrap=True, max_depth=10, max_features=sqrt, min_samples_leaf=2, min_samples_split=5, n_estimators=1000;, score=0.744 total time= 1.1min
[CV 1/3; 80/100] START bootstrap=True, max_depth=80, max_features=auto, min_samples_leaf=4, min_samples_split=5, n_estimators=200
[CV 1/3; 80/100] END bootstrap=True, max_depth=80, max_features=auto, min_samples_leaf=4, min_samples_split=5, n_estimators=200;, score=0.787 total time=  15.3s
[CV 3/3; 80/100] START bootstrap=True, max_depth=80, max_features=auto, min_samples_leaf=4, min_samples_split=5, n_estimators=200
[CV 3/3; 80/100] END bootstrap=True, max_depth=80, max_features=auto, min_samples_leaf=4, min_samples_split=5, n_estimators=200;, score=0.782 total time= 3.6min
[CV 2/3; 82/100] START bootstrap=True, max_depth=100, max_features=auto, min_samples_leaf=2, min_samples_split=10, n_estimato

/Users/angeloturri/opt/anaconda3/envs/learn-env/lib/python3.11/site-packages/sklearn/utils/validation.py:767: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if not hasattr(array, "sparse") and array.dtypes.apply(is_sparse).any():
/Users/angeloturri/opt/anaconda3/envs/learn-env/lib/python3.11/site-packages/sklearn/utils/validation.py:605: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(pd_dtype):
/Users/angeloturri/opt/anaconda3/envs/learn-env/lib/python3.11/site-packages/sklearn/utils/validation.py:614: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(pd_dtype) or not is_extension_array_dtype(pd_dtype):
/Users/angeloturri/opt/anaconda3/envs/learn-env/lib/python3.11/site-packages/sklearn/utils/validation.py:767

/Users/angeloturri/opt/anaconda3/envs/learn-env/lib/python3.11/site-packages/sklearn/utils/validation.py:767: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if not hasattr(array, "sparse") and array.dtypes.apply(is_sparse).any():
/Users/angeloturri/opt/anaconda3/envs/learn-env/lib/python3.11/site-packages/sklearn/utils/validation.py:605: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(pd_dtype):
/Users/angeloturri/opt/anaconda3/envs/learn-env/lib/python3.11/site-packages/sklearn/utils/validation.py:614: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(pd_dtype) or not is_extension_array_dtype(pd_dtype):
/Users/angeloturri/opt/anaconda3/envs/learn-env/lib/python3.11/site-packages/sklearn/utils/validation.py:767

RandomizedSearchCV(cv=3, estimator=RandomForestClassifier(), n_iter=100,
                   n_jobs=-1,
                   param_distributions={'bootstrap': [True, False],
                                        'max_depth': [10, 20, 30, 40, 50, 60,
                                                      70, 80, 90, 100, 110,
                                                      None],
                                        'max_features': ['auto', 'sqrt'],
                                        'min_samples_leaf': [1, 2, 4],
                                        'min_samples_split': [2, 5, 10],
                                        'n_estimators': [200, 400, 600, 800,
                                                         1000, 1200, 1400, 1600,
                                                         1800, 2000]},
                   random_state=42, verbose=10)

In [276]:
rf_random.best_params_

{'n_estimators': 400,
 'min_samples_split': 5,
 'min_samples_leaf': 1,
 'max_features': 'sqrt',
 'max_depth': 30,
 'bootstrap': True}

In [282]:
best_forest = RandomForestClassifier(n_estimators=400, min_samples_split=5, min_samples_leaf=1, max_features='sqrt', max_depth=30, bootstrap=True)

[CV 2/3; 75/100] START bootstrap=True, max_depth=90, max_features=auto, min_samples_leaf=1, min_samples_split=5, n_estimators=1600
[CV 2/3; 75/100] END bootstrap=True, max_depth=90, max_features=auto, min_samples_leaf=1, min_samples_split=5, n_estimators=1600;, score=0.800 total time= 3.2min
[CV 1/3; 79/100] START bootstrap=True, max_depth=10, max_features=sqrt, min_samples_leaf=2, min_samples_split=5, n_estimators=1000
[CV 1/3; 79/100] END bootstrap=True, max_depth=10, max_features=sqrt, min_samples_leaf=2, min_samples_split=5, n_estimators=1000;, score=0.743 total time= 1.1min
[CV 3/3; 79/100] START bootstrap=True, max_depth=10, max_features=sqrt, min_samples_leaf=2, min_samples_split=5, n_estimators=1000
[CV 3/3; 79/100] END bootstrap=True, max_depth=10, max_features=sqrt, min_samples_leaf=2, min_samples_split=5, n_estimators=1000;, score=0.738 total time= 4.0min
[CV 1/3; 82/100] START bootstrap=True, max_depth=100, max_features=auto, min_samples_leaf=2, min_samples_split=10, n_esti

[CV 3/3; 66/100] START bootstrap=True, max_depth=None, max_features=auto, min_samples_leaf=2, min_samples_split=10, n_estimators=1600
[CV 3/3; 66/100] END bootstrap=True, max_depth=None, max_features=auto, min_samples_leaf=2, min_samples_split=10, n_estimators=1600;, score=0.790 total time= 2.2min
[CV 2/3; 70/100] START bootstrap=False, max_depth=60, max_features=auto, min_samples_leaf=2, min_samples_split=10, n_estimators=2000
[CV 2/3; 70/100] END bootstrap=False, max_depth=60, max_features=auto, min_samples_leaf=2, min_samples_split=10, n_estimators=2000;, score=0.801 total time= 4.6min
[CV 3/3; 73/100] START bootstrap=True, max_depth=60, max_features=sqrt, min_samples_leaf=2, min_samples_split=5, n_estimators=1800
[CV 3/3; 73/100] END bootstrap=True, max_depth=60, max_features=sqrt, min_samples_leaf=2, min_samples_split=5, n_estimators=1800;, score=0.794 total time= 2.8min
[CV 1/3; 78/100] START bootstrap=True, max_depth=100, max_features=sqrt, min_samples_leaf=1, min_samples_split=

In [308]:
best_forest.fit(X_train,y_train)

RandomForestClassifier(max_depth=30, min_samples_split=5, n_estimators=400)

In [281]:
best_forest_preds = best_forest.predict(X_test)

In [283]:
pd.DataFrame(classification_report(y_test, best_forest_preds, output_dict=True))

0            1            2  accuracy     macro avg  \
precision     0.584369     0.836524     0.802825  0.806397      0.741239   
recall        0.295863     0.775786     0.897717  0.806397      0.656455   
f1-score      0.392836     0.805011     0.847623  0.806397      0.681823   
support    1112.000000  5633.000000  8105.000000  0.806397  14850.000000   

           weighted avg  
precision      0.799249  
recall         0.806397  
f1-score       0.797404  
support    14850.000000

In [284]:
pd.DataFrame(confusion_matrix(y_test, best_forest_preds))

0     1     2
0  329   185   598
1   74  4370  1189
2  160   669  7276

In [293]:
second_best_forest = RandomForestClassifier()
X_train_resampled, y_train_resampled = SMOTE(sampling_strategy={0:10000}).fit_resample(X_train, y_train)
second_best_forest.fit(X_train_resampled, y_train_resampled)

RandomForestClassifier()

In [294]:
second_best_forest_preds = second_best_forest.predict(X_test)

In [295]:
pd.DataFrame(classification_report(y_test, second_best_forest_preds, output_dict=True))

0            1            2  accuracy     macro avg  \
precision     0.434031     0.821269     0.821954  0.792997      0.692418   
recall        0.428957     0.785549     0.848118  0.792997      0.687542   
f1-score      0.431479     0.803012     0.834831  0.792997      0.689774   
support    1112.000000  5633.000000  8105.000000  0.792997  14850.000000   

           weighted avg  
precision      0.792646  
recall         0.792997  
f1-score       0.792558  
support    14850.000000

In [296]:
pd.DataFrame(confusion_matrix(y_test, second_best_forest_preds))

0     1     2
0  477   176   459
1  178  4425  1030
2  444   787  6874

In [304]:
decisions = []

for a, b in list(zip(best_forest_preds, second_best_forest_preds)):
    if b==0:
        decision=0
    elif a==2:
        decision=2
    else:
        decision=1
    decisions.append(decision)

In [305]:
pd.DataFrame(classification_report(y_test, decisions, output_dict=True))

0            1            2  accuracy     macro avg  \
precision     0.434031     0.843707     0.813819  0.796027      0.697186   
recall        0.428957     0.767619     0.866132  0.796027      0.687569   
f1-score      0.431479     0.803867     0.839161  0.796027      0.691502   
support    1112.000000  5633.000000  8105.000000  0.796027  14850.000000   

           weighted avg  
precision      0.796717  
recall         0.796027  
f1-score       0.795245  
support    14850.000000

In [309]:
pd.DataFrame(classification_report(y_train, best_forest.predict(X_train), output_dict=True))

0             1             2  accuracy     macro avg  \
precision     0.922164      0.960552      0.901827  0.924175      0.928181   
recall        0.606240      0.906521      0.978927  0.924175      0.830563   
f1-score      0.731551      0.932755      0.938797  0.924175      0.867701   
support    3205.000000  17191.000000  24154.000000  0.924175  44550.000000   

           weighted avg  
precision      0.925951  
recall         0.924175  
f1-score       0.921556  
support    44550.000000

In [310]:
pd.DataFrame(classification_report(y_train, second_best_forest.predict(X_train), output_dict=True))

0             1             2  accuracy     macro avg  \
precision     0.947054      0.999300      0.997256  0.994276      0.981203   
recall        0.987832      0.997150      0.993086  0.994276      0.992689   
f1-score      0.967013      0.998224      0.995167  0.994276      0.986801   
support    3205.000000  17191.000000  24154.000000  0.994276  44550.000000   

           weighted avg  
precision      0.994433  
recall         0.994276  
f1-score       0.994321  
support    44550.000000

In [ ]:
# Use the random grid to search for best hyperparameters
# First create the base model to tune
rf = RandomForestClassifier()
# Random search of parameters, using 3 fold cross validation, 
# search across 100 different combinations, and use all available cores
rf_random = RandomizedSearchCV(estimator = rf, param_distributions = random_grid, n_iter = 100, cv = 3, verbose=10, random_state=42, n_jobs = -1)
# Fit the random search model
rf_random.fit(X_train, y_train)

In [326]:
X_sample = X_train_resampled.sample(n=1000,random_state=42)
y_sample = y_train_resampled.take(X_sample.index)

In [327]:
# Use the random grid to search for best hyperparameters
# First create the base model to tune
rf = RandomForestClassifier()
# Random search of parameters, using 3 fold cross validation, 
# search across 100 different combinations, and use all available cores
rf_random = RandomizedSearchCV(estimator = rf, param_distributions = random_grid, n_iter = 100, cv = 3, verbose=10, random_state=42, n_jobs = -1)
# Fit the random search model
rf_random.fit(X_sample, y_sample)

Fitting 3 folds for each of 100 candidates, totalling 300 fits


/Users/angeloturri/opt/anaconda3/envs/learn-env/lib/python3.11/site-packages/sklearn/utils/validation.py:767: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if not hasattr(array, "sparse") and array.dtypes.apply(is_sparse).any():
/Users/angeloturri/opt/anaconda3/envs/learn-env/lib/python3.11/site-packages/sklearn/utils/validation.py:767: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if not hasattr(array, "sparse") and array.dtypes.apply(is_sparse).any():
/Users/angeloturri/opt/anaconda3/envs/learn-env/lib/python3.11/site-packages/sklearn/utils/validation.py:767: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if not hasattr(array, "sparse") and array.dtypes.apply(is_sparse).any():
/Users/angeloturri/opt/anaconda3/envs/learn-env/lib/

/Users/angeloturri/opt/anaconda3/envs/learn-env/lib/python3.11/site-packages/sklearn/utils/validation.py:767: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if not hasattr(array, "sparse") and array.dtypes.apply(is_sparse).any():
/Users/angeloturri/opt/anaconda3/envs/learn-env/lib/python3.11/site-packages/sklearn/utils/validation.py:767: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if not hasattr(array, "sparse") and array.dtypes.apply(is_sparse).any():
/Users/angeloturri/opt/anaconda3/envs/learn-env/lib/python3.11/site-packages/sklearn/utils/validation.py:605: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(pd_dtype):
/Users/angeloturri/opt/anaconda3/envs/learn-env/lib/python3.11/site-packages/sklearn/utils/validation

/Users/angeloturri/opt/anaconda3/envs/learn-env/lib/python3.11/site-packages/sklearn/utils/validation.py:767: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if not hasattr(array, "sparse") and array.dtypes.apply(is_sparse).any():
/Users/angeloturri/opt/anaconda3/envs/learn-env/lib/python3.11/site-packages/sklearn/utils/validation.py:605: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(pd_dtype):
/Users/angeloturri/opt/anaconda3/envs/learn-env/lib/python3.11/site-packages/sklearn/utils/validation.py:614: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(pd_dtype) or not is_extension_array_dtype(pd_dtype):
/Users/angeloturri/opt/anaconda3/envs/learn-env/lib/python3.11/site-packages/sklearn/utils/validation.py:767

/Users/angeloturri/opt/anaconda3/envs/learn-env/lib/python3.11/site-packages/sklearn/utils/validation.py:767: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if not hasattr(array, "sparse") and array.dtypes.apply(is_sparse).any():
/Users/angeloturri/opt/anaconda3/envs/learn-env/lib/python3.11/site-packages/sklearn/utils/validation.py:605: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(pd_dtype):
/Users/angeloturri/opt/anaconda3/envs/learn-env/lib/python3.11/site-packages/sklearn/utils/validation.py:614: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(pd_dtype) or not is_extension_array_dtype(pd_dtype):
/Users/angeloturri/opt/anaconda3/envs/learn-env/lib/python3.11/site-packages/sklearn/utils/validation.py:605

...

/Users/angeloturri/opt/anaconda3/envs/learn-env/lib/python3.11/site-packages/sklearn/utils/validation.py:767: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if not hasattr(array, "sparse") and array.dtypes.apply(is_sparse).any():
/Users/angeloturri/opt/anaconda3/envs/learn-env/lib/python3.11/site-packages/sklearn/utils/validation.py:605: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(pd_dtype):
/Users/angeloturri/opt/anaconda3/envs/learn-env/lib/python3.11/site-packages/sklearn/utils/validation.py:614: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(pd_dtype) or not is_extension_array_dtype(pd_dtype):
/Users/angeloturri/opt/anaconda3/envs/learn-env/lib/python3.11/site-packages/sklearn/utils/validation.py:767

/Users/angeloturri/opt/anaconda3/envs/learn-env/lib/python3.11/site-packages/sklearn/utils/validation.py:767: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if not hasattr(array, "sparse") and array.dtypes.apply(is_sparse).any():
/Users/angeloturri/opt/anaconda3/envs/learn-env/lib/python3.11/site-packages/sklearn/utils/validation.py:767: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if not hasattr(array, "sparse") and array.dtypes.apply(is_sparse).any():
/Users/angeloturri/opt/anaconda3/envs/learn-env/lib/python3.11/site-packages/sklearn/utils/validation.py:605: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(pd_dtype):
/Users/angeloturri/opt/anaconda3/envs/learn-env/lib/python3.11/site-packages/sklearn/utils/validation

/Users/angeloturri/opt/anaconda3/envs/learn-env/lib/python3.11/site-packages/sklearn/utils/validation.py:605: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(pd_dtype):
/Users/angeloturri/opt/anaconda3/envs/learn-env/lib/python3.11/site-packages/sklearn/utils/validation.py:614: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(pd_dtype) or not is_extension_array_dtype(pd_dtype):
/Users/angeloturri/opt/anaconda3/envs/learn-env/lib/python3.11/site-packages/sklearn/utils/validation.py:605: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(pd_dtype):
/Users/angeloturri/opt/anaconda3/envs/learn-env/lib/python3.11/site-packages/sklearn/utils/validation.py:614: FutureWarning: is_sparse is deprecated and will

/Users/angeloturri/opt/anaconda3/envs/learn-env/lib/python3.11/site-packages/sklearn/utils/validation.py:767: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if not hasattr(array, "sparse") and array.dtypes.apply(is_sparse).any():
/Users/angeloturri/opt/anaconda3/envs/learn-env/lib/python3.11/site-packages/sklearn/utils/validation.py:605: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(pd_dtype):
/Users/angeloturri/opt/anaconda3/envs/learn-env/lib/python3.11/site-packages/sklearn/utils/validation.py:614: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(pd_dtype) or not is_extension_array_dtype(pd_dtype):
/Users/angeloturri/opt/anaconda3/envs/learn-env/lib/python3.11/site-packages/sklearn/utils/validation.py:605

RandomizedSearchCV(cv=3, estimator=RandomForestClassifier(), n_iter=100,
                   n_jobs=-1,
                   param_distributions={'bootstrap': [True, False],
                                        'max_depth': [10, 20, 30, 40, 50, 60,
                                                      70, 80, 90, 100, 110,
                                                      None],
                                        'max_features': ['auto', 'sqrt'],
                                        'min_samples_leaf': [1, 2, 4],
                                        'min_samples_split': [2, 5, 10],
                                        'n_estimators': [200, 400, 600, 800,
                                                         1000, 1200, 1400, 1600,
                                                         1800, 2000]},
                   random_state=42, verbose=10)

In [328]:
rf_random.best_params_

{'n_estimators': 2000,
 'min_samples_split': 2,
 'min_samples_leaf': 2,
 'max_features': 'auto',
 'max_depth': 90,
 'bootstrap': True}

In [372]:
f1_scores=[]

for ratio in np.linspace(4000,100000,97,dtype='int64'):
    
    print(f"Sample: #{ratio}")
    clear_output(wait=True)
    
    strategy = {0:ratio}
    smote = SMOTE(sampling_strategy=strategy)
    X_train_resampled, y_train_resampled = smote.fit_resample(X_train, y_train)
    estimator = RandomForestClassifier()
    estimator.fit(X_train_resampled, y_train_resampled)
    preds = estimator.predict(X_test)
    f1 = f1_score(y_test, preds, average=None)
    f1_scores.append(f1

Sample: #100000


In [414]:
ratiodf = pd.DataFrame({'ratio': np.linspace(4000,100000,97,dtype='int64'), 
              'f1_score_fnr': [i[0] for i in f1_scores], 
              'f1_score_nf': [i[1] for i in f1_scores], 
              'f1_score_f': [i[2] for i in f1_scores]})

In [430]:
smote=SMOTE(sampling_strategy={0:10000})
X_train_resampled, y_train_resampled = smote.fit_resample(X_train, y_train)
estimator=RandomForestClassifier(random_state=42)
estimator.fit(X_train_resampled, y_train_resampled)
preds = estimator.predict(X_test)

In [431]:
pd.DataFrame(classification_report(y_test, preds, output_dict=True))

0            1            2  accuracy     macro avg  \
precision     0.439353     0.824758     0.824077  0.795488      0.696063   
recall        0.439748     0.785372     0.851326  0.795488      0.692149   
f1-score      0.439551     0.804583     0.837480  0.795488      0.693871   
support    1112.000000  5633.000000  8105.000000  0.795488  14850.000000   

           weighted avg  
precision      0.795526  
recall         0.795488  
f1-score       0.795204  
support    14850.000000

In [433]:
# Use the random grid to search for best hyperparameters
# First create the base model to tune
rf = RandomForestClassifier()
# Random search of parameters, using 3 fold cross validation, 
# search across 100 different combinations, and use all available cores
rf_random = RandomizedSearchCV(estimator = rf, param_distributions = random_grid, n_iter = 100, cv = 3, verbose=10, random_state=42, n_jobs = -1)
# Fit the random search model
rf_random.fit(X_train_resampled, y_train_resampled)

Fitting 3 folds for each of 100 candidates, totalling 300 fits


/Users/angeloturri/opt/anaconda3/envs/learn-env/lib/python3.11/site-packages/sklearn/utils/validation.py:767: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if not hasattr(array, "sparse") and array.dtypes.apply(is_sparse).any():
/Users/angeloturri/opt/anaconda3/envs/learn-env/lib/python3.11/site-packages/sklearn/utils/validation.py:605: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(pd_dtype):
/Users/angeloturri/opt/anaconda3/envs/learn-env/lib/python3.11/site-packages/sklearn/utils/validation.py:614: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(pd_dtype) or not is_extension_array_dtype(pd_dtype):
/Users/angeloturri/opt/anaconda3/envs/learn-env/lib/python3.11/site-packages/sklearn/utils/validation.py:767

/Users/angeloturri/opt/anaconda3/envs/learn-env/lib/python3.11/site-packages/sklearn/utils/validation.py:767: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if not hasattr(array, "sparse") and array.dtypes.apply(is_sparse).any():
/Users/angeloturri/opt/anaconda3/envs/learn-env/lib/python3.11/site-packages/sklearn/utils/validation.py:605: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(pd_dtype):
/Users/angeloturri/opt/anaconda3/envs/learn-env/lib/python3.11/site-packages/sklearn/utils/validation.py:614: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(pd_dtype) or not is_extension_array_dtype(pd_dtype):
/Users/angeloturri/opt/anaconda3/envs/learn-env/lib/python3.11/site-packages/sklearn/utils/validation.py:767

/Users/angeloturri/opt/anaconda3/envs/learn-env/lib/python3.11/site-packages/sklearn/utils/validation.py:767: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if not hasattr(array, "sparse") and array.dtypes.apply(is_sparse).any():
/Users/angeloturri/opt/anaconda3/envs/learn-env/lib/python3.11/site-packages/sklearn/utils/validation.py:605: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(pd_dtype):
/Users/angeloturri/opt/anaconda3/envs/learn-env/lib/python3.11/site-packages/sklearn/utils/validation.py:614: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(pd_dtype) or not is_extension_array_dtype(pd_dtype):
/Users/angeloturri/opt/anaconda3/envs/learn-env/lib/python3.11/site-packages/sklearn/utils/validation.py:605

/Users/angeloturri/opt/anaconda3/envs/learn-env/lib/python3.11/site-packages/sklearn/utils/validation.py:614: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(pd_dtype) or not is_extension_array_dtype(pd_dtype):
/Users/angeloturri/opt/anaconda3/envs/learn-env/lib/python3.11/site-packages/sklearn/ensemble/_forest.py:424: FutureWarning: `max_features='auto'` has been deprecated in 1.1 and will be removed in 1.3. To keep the past behaviour, explicitly set `max_features='sqrt'` or remove this parameter as it is also the default value for RandomForestClassifiers and ExtraTreesClassifiers.
  warn(
/Users/angeloturri/opt/anaconda3/envs/learn-env/lib/python3.11/site-packages/sklearn/utils/validation.py:605: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(pd_dtype):
/Users/angeloturri/opt/anaconda3/envs

...

[CV 1/3; 63/100] START bootstrap=False, max_depth=80, max_features=auto, min_samples_leaf=4, min_samples_split=10, n_estimators=1000
[CV 1/3; 63/100] END bootstrap=False, max_depth=80, max_features=auto, min_samples_leaf=4, min_samples_split=10, n_estimators=1000;, score=0.760 total time= 2.3min
[CV 1/3; 66/100] START bootstrap=True, max_depth=None, max_features=auto, min_samples_leaf=2, min_samples_split=10, n_estimators=1600
[CV 1/3; 66/100] END bootstrap=True, max_depth=None, max_features=auto, min_samples_leaf=2, min_samples_split=10, n_estimators=1600;, score=0.765 total time= 2.7min
[CV 1/3; 69/100] START bootstrap=False, max_depth=80, max_features=sqrt, min_samples_leaf=1, min_samples_split=10, n_estimators=1000
[CV 1/3; 69/100] END bootstrap=False, max_depth=80, max_features=sqrt, min_samples_leaf=1, min_samples_split=10, n_estimators=1000;, score=0.778 total time= 3.0min
[CV 3/3; 71/100] START bootstrap=False, max_depth=80, max_features=sqrt, min_samples_leaf=4, min_samples_sp

/Users/angeloturri/opt/anaconda3/envs/learn-env/lib/python3.11/site-packages/sklearn/utils/validation.py:605: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(pd_dtype):
/Users/angeloturri/opt/anaconda3/envs/learn-env/lib/python3.11/site-packages/sklearn/utils/validation.py:614: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(pd_dtype) or not is_extension_array_dtype(pd_dtype):
/Users/angeloturri/opt/anaconda3/envs/learn-env/lib/python3.11/site-packages/sklearn/utils/validation.py:605: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(pd_dtype):
/Users/angeloturri/opt/anaconda3/envs/learn-env/lib/python3.11/site-packages/sklearn/utils/validation.py:614: FutureWarning: is_sparse is deprecated and will

[CV 1/3; 36/100] START bootstrap=False, max_depth=20, max_features=sqrt, min_samples_leaf=2, min_samples_split=10, n_estimators=800
[CV 1/3; 36/100] END bootstrap=False, max_depth=20, max_features=sqrt, min_samples_leaf=2, min_samples_split=10, n_estimators=800;, score=0.757 total time= 1.6min
[CV 3/3; 37/100] START bootstrap=True, max_depth=20, max_features=sqrt, min_samples_leaf=2, min_samples_split=5, n_estimators=1200
[CV 3/3; 37/100] END bootstrap=True, max_depth=20, max_features=sqrt, min_samples_leaf=2, min_samples_split=5, n_estimators=1200;, score=0.783 total time= 1.8min
[CV 2/3; 40/100] START bootstrap=True, max_depth=60, max_features=sqrt, min_samples_leaf=2, min_samples_split=2, n_estimators=1000
[CV 2/3; 40/100] END bootstrap=True, max_depth=60, max_features=sqrt, min_samples_leaf=2, min_samples_split=2, n_estimators=1000;, score=0.805 total time= 1.8min
[CV 1/3; 45/100] START bootstrap=False, max_depth=90, max_features=auto, min_samples_leaf=2, min_samples_split=5, n_est

[CV 2/3; 84/100] START bootstrap=False, max_depth=None, max_features=auto, min_samples_leaf=2, min_samples_split=10, n_estimators=800
[CV 2/3; 84/100] END bootstrap=False, max_depth=None, max_features=auto, min_samples_leaf=2, min_samples_split=10, n_estimators=800;, score=0.811 total time= 2.0min
[CV 3/3; 86/100] START bootstrap=False, max_depth=40, max_features=sqrt, min_samples_leaf=1, min_samples_split=10, n_estimators=600
[CV 3/3; 86/100] END bootstrap=False, max_depth=40, max_features=sqrt, min_samples_leaf=1, min_samples_split=10, n_estimators=600;, score=0.826 total time= 1.8min
[CV 2/3; 90/100] START bootstrap=True, max_depth=10, max_features=sqrt, min_samples_leaf=2, min_samples_split=10, n_estimators=1000
[CV 2/3; 90/100] END bootstrap=True, max_depth=10, max_features=sqrt, min_samples_leaf=2, min_samples_split=10, n_estimators=1000;, score=0.696 total time=  50.0s
[CV 2/3; 91/100] START bootstrap=True, max_depth=110, max_features=sqrt, min_samples_leaf=1, min_samples_split=

RandomizedSearchCV(cv=3, estimator=RandomForestClassifier(), n_iter=100,
                   n_jobs=-1,
                   param_distributions={'bootstrap': [True, False],
                                        'max_depth': [10, 20, 30, 40, 50, 60,
                                                      70, 80, 90, 100, 110,
                                                      None],
                                        'max_features': ['auto', 'sqrt'],
                                        'min_samples_leaf': [1, 2, 4],
                                        'min_samples_split': [2, 5, 10],
                                        'n_estimators': [200, 400, 600, 800,
                                                         1000, 1200, 1400, 1600,
                                                         1800, 2000]},
                   random_state=42, verbose=10)

In [435]:
rf_random.best_params_

{'n_estimators': 2000,
 'min_samples_split': 5,
 'min_samples_leaf': 1,
 'max_features': 'sqrt',
 'max_depth': 100,
 'bootstrap': True}

In [436]:
fourth_best_forest = RandomForestClassifier(n_estimators=2000, min_samples_split=5, min_samples_leaf=1, max_features='sqrt', max_depth=100, bootstrap=True)

In [437]:
fourth_best_forest.fit(X_train_resampled, y_train_resampled)

RandomForestClassifier(max_depth=100, min_samples_split=5, n_estimators=2000)

In [438]:
fourth_best_preds = fourth_best_forest.predict(X_test)

In [439]:
pd.DataFrame(classification_report(y_test, fourth_best_preds, output_dict=True))

0            1            2  accuracy     macro avg  \
precision     0.461101     0.839655     0.818447  0.800539      0.706401   
recall        0.437050     0.778093     0.866009  0.800539      0.693717   
f1-score      0.448753     0.807703     0.841556  0.800539      0.699338   
support    1112.000000  5633.000000  8105.000000  0.800539  14850.000000   

           weighted avg  
precision      0.799733  
recall         0.800539  
f1-score       0.799301  
support    14850.000000